In [27]:
from __future__ import division, print_function
import numpy as np
import pandas as pd
import geopandas as gpd
import holoviews as hv
import geoviews as gv
import cartopy
from bokeh.models import WMTSTileSource

from cartopy import crs
from cartopy import feature as cf
from geoviews import feature as gf

hv.notebook_extension('bokeh')
%output backend='bokeh'
%opts Feature [projection=crs.PlateCarree()]

In [2]:
ward_df = gpd.read_file('business_street_exemptions/ward_boundaries.geojson')
ward_shp = 'business_street_exemptions/ward_boundaries.shp'
ward_df.to_file(ward_shp, driver='ESRI Shapefile')

In [8]:
ward_tickets = pd.read_csv('taxi_ticket_data/taxi_tickets_by_ward.csv')
tickets_by_ward = pd.DataFrame(ward_tickets.groupby(['Ward'])['Ticket Number'].count()).reset_index()
tickets_by_ward = tickets_by_ward.rename(columns={'Ward':'ward','Ticket Number':'taxi_tickets'})
tickets_by_ward['ward'] = tickets_by_ward['ward'].astype(str)

# For some reason, GeoViews does not convert integers to floats for display, integers will not have differently 
# colored values based on range, so need to convert to float
tickets_by_ward['taxi_tickets'] = tickets_by_ward['taxi_tickets'].astype(float)
tickets_by_ward = tickets_by_ward[tickets_by_ward['ward'] != '0']
tickets_by_ward.head()

ward  taxi_tickets
1    1        1703.0
2    2       17305.0
3    3       17477.0
4    4        4338.0
5    5        1756.0

In [37]:
%%opts Shape (cmap='YlOrRd', line_color='grey', line_width=0.1) [xaxis=None yaxis=None tools=['hover'] width=600 height=500]
ward_shapes = cartopy.io.shapereader.Reader(ward_shp)
tickets = hv.Dataset(tickets_by_ward)
gv.Shape.from_records(ward_shapes.records(), tickets, on='ward', value='taxi_tickets',
                      index=['ward', 'taxi_tickets'], crs=crs.PlateCarree()) * gv.WMTS(WMTSTileSource(url='https://maps.wikimedia.org/osm-intl/{Z}/{X}/{Y}@2x.png'))

:Overlay
   .NdOverlay.I :NdOverlay   [ward,taxi_tickets]
      :Shape   [Longitude,Latitude]   (taxi_tickets)
   .WMTS.I      :WMTS   [Longitude,Latitude]